In [337]:
import pandas as pd
import numpy as np

# Read the data
data = pd.read_csv('Walmart.csv')
# make date year-month-day int
data['Date'] = pd.to_numeric(pd.to_datetime(data['Date']))

# holiday_flag is binary
data['Holiday_Flag'] = data['Holiday_Flag'].astype('category')
# make store column categorical
data['Store'] = data['Store'].astype('category')

/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/pandas/core/tools/datetimes.py:1047: UserWarning: Parsing '19-02-2010' in DD/MM/YYYY format. Provide format or specify infer_datetime_format=True for consistent parsing.
  cache_array = _maybe_cache(arg, format, cache, convert_listlike)
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/pandas/core/tools/datetimes.py:1047: UserWarning: Parsing '26-02-2010' in DD/MM/YYYY format. Provide format or specify infer_datetime_format=True for consistent parsing.
  cache_array = _maybe_cache(arg, format, cache, convert_listlike)
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/pandas/core/tools/datetimes.py:1047: UserWarning: Parsing '19-03-2010' in DD/MM/YYYY format. Provide format or specify infer_datetime_format=True for consistent parsing.
  cache_array = _maybe_cache(arg, format, cache, convert_listlike)
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/pandas/core/tools/datetimes.py:1047: UserWarning: Par

In [338]:
# split the data into train and test
from sklearn.model_selection import train_test_split
# remove store 45 and call it's data to_prescribe
#data= data.drop(['Store'], axis=1)
# split into train, test, and new by date - .6,.3,.1
train = data[data['Date'] < data['Date'].quantile(0.65)]
test = data[(data['Date'] >= data['Date'].quantile(0.65)) & (data['Date'] < data['Date'].quantile(0.98))]
new = data[data['Date'] >= data['Date'].quantile(0.98)]
X_train = train.drop('Weekly_Sales', axis=1)
y_train = train['Weekly_Sales']
X_test = test.drop('Weekly_Sales', axis=1)
y_test = test['Weekly_Sales']

In [339]:
train_total = data[data['Date'] < data['Date'].quantile(0.9)]
X_train_total = train_total.drop('Weekly_Sales', axis=1)
y_train_total = train_total['Weekly_Sales']

In [190]:
new

Store       Date  Weekly_Sales Holiday_Flag  Temperature  Fuel_Price  \
118      1 2012-11-05    1611096.05            0        73.77       3.688   
140      1 2012-12-10    1573072.81            0        62.99       3.601   
142      1 2012-10-26    1493659.74            0        69.16       3.506   
261      2 2012-11-05    1917520.99            0        73.87       3.688   
283      2 2012-12-10    1900745.13            0        60.97       3.601   
...    ...        ...           ...          ...          ...         ...   
6289    44 2012-12-10     337796.13            0        55.10       3.797   
6291    44 2012-10-26     361067.07            0        46.97       3.755   
6410    45 2012-11-05     770487.37            0        61.24       3.889   
6432    45 2012-12-10     734464.36            0        54.47       4.000   
6434    45 2012-10-26     760281.43            0        58.85       3.882   

             CPI  Unemployment  
118   221.725663         7.143  
140   223.381296         6.573  
142   223.444251         6.573  
261   221.363221         6.891  
283   223.015426         6.170  
...          ...           ...  
6289  131.108333         5.217  
6291  131.193097         5.217  
6410  190.976417         8.567  
6432  192.327265         8.667  
6434  192.308899         8.667  

[135 rows x 8 columns]

In [150]:
# write indices of train_total to csv
train_total.to_csv('train_total.csv', index=True)

In [309]:
# load in pred and predNew
pred = pd.read_csv('Node.csv')
predNew = pd.read_csv('NewNode.csv')
#pred = remove index and Unnamed: 2
pred = pred.drop(['index'], axis=1)
nodes = predNew.drop(['index'], axis=1)

In [342]:
# cart model
from sklearn.tree import DecisionTreeRegressor

cart_model = DecisionTreeRegressor(random_state=42, min_samples_leaf=40).fit(X_train, y_train)
y_pred = cart_model.predict(X_test)

In [343]:
# score the model
from sklearn.metrics import mean_squared_error, r2_score
# set random seed
np.random.seed(123)
print('MSE: ', mean_squared_error(y_test, y_pred))
print('R2: ', r2_score(y_test, y_pred))

MSE:  108015780274.57492
R2:  0.6724500285784358


In [260]:
pred

node
0     1.397221e+06
1     1.397221e+06
2     1.397221e+06
3     1.397221e+06
4     1.397221e+06
...            ...
5755  8.010039e+05
5756  8.010039e+05
5757  8.010039e+05
5758  8.010039e+05
5759  8.010039e+05

[5760 rows x 1 columns]

In [344]:
y_train_total = y_train_total.reset_index(drop=True)

In [345]:
new = new.reset_index(drop=True)

In [280]:
new

Store       Date  Weekly_Sales Holiday_Flag  Temperature  Fuel_Price  \
0       1 2012-11-05    1611096.05            0        73.77       3.688   
1       1 2012-12-10    1573072.81            0        62.99       3.601   
2       1 2012-10-26    1493659.74            0        69.16       3.506   
3       2 2012-11-05    1917520.99            0        73.87       3.688   
4       2 2012-12-10    1900745.13            0        60.97       3.601   
..    ...        ...           ...          ...          ...         ...   
130    44 2012-12-10     337796.13            0        55.10       3.797   
131    44 2012-10-26     361067.07            0        46.97       3.755   
132    45 2012-11-05     770487.37            0        61.24       3.889   
133    45 2012-12-10     734464.36            0        54.47       4.000   
134    45 2012-10-26     760281.43            0        58.85       3.882   

            CPI  Unemployment  
0    221.725663         7.143  
1    223.381296         6.573  
2    223.444251         6.573  
3    221.363221         6.891  
4    223.015426         6.170  
..          ...           ...  
130  131.108333         5.217  
131  131.193097         5.217  
132  190.976417         8.567  
133  192.327265         8.667  
134  192.308899         8.667  

[135 rows x 8 columns]

In [348]:
# gurobi
from gurobipy import *
nodes = cart_model.apply(new.drop('Weekly_Sales', axis=1))
total_profit = 0
row = 0
for node in nodes:
    # n20 = y_train of elements who's pred is node
    n20 = y_train_total[cart_model.apply(X_train_total) == node]
    # reset index
    n20 = n20.reset_index()
    # drop index
    n20 = n20.drop(['index'], axis=1)
    # Create a new model
    m = Model("mip1")
    # variable z
    z = m.addVar(vtype=GRB.CONTINUOUS, name="z", lb=0)
    # variable q
    q = m.addVar(vtype=GRB.CONTINUOUS, name="q", lb=0)
    # variable r that is array of size n20
    #r = m.addVars(n20.shape[0], vtype=GRB.CONTINUOUS, name="r", lb=0)
    # variable p - vector size(n20)
    sold = m.addVars(n20.shape[0], vtype=GRB.CONTINUOUS, name="p", lb=0)
    # variable r - vector size(n20)
    #unmet = m.addVars(n20.shape[0], vtype=GRB.CONTINUOUS, name="unment", lb=0)
    # objective, for i in n20, z*(100/19)-min(i,z*3)
    m.setObjective(quicksum(sold[i]-z*(19/100) for i in range(n20.shape[0])), GRB.MAXIMIZE)
    # p[i] = min(i,z*3)
    m.addConstrs((sold[i] == min_(q, constant=n20.loc[i]) for i in range(n20.shape[0])), "c")
    # z = q+r
    #m.addConstrs((unmet[i] == min_(r[i], constant=0) for i in range(n20.shape[0])), "c")
    #m.addConstr((r[i] == q - n20.loc[i] for i in range(n20.shape[0])), "c")
    # z = q
    m.addConstr(z*3 == q, "c2")

    # Optimize model
    m.optimize()
    
    profit = min(q.x, new.loc[row]['Weekly_Sales']) - z.x*(19/100)
    row += 1
    total_profit += profit


Gurobi Optimizer version 9.5.2 build v9.5.2rc0 (mac64[rosetta2])
Thread count: 8 physical cores, 8 logical processors, using up to 8 threads
Optimize a model with 1 rows, 71 columns and 2 nonzeros
Model fingerprint: 0x99edf93f
Model has 69 general constraints
Variable types: 71 continuous, 0 integer (0 binary)
Coefficient statistics:
  Matrix range     [1e+00, 3e+00]
  Objective range  [1e+00, 1e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [0e+00, 0e+00]
  GenCon const rng [1e+06, 2e+06]
Found heuristic solution: objective -0.0000000
Presolve removed 1 rows and 71 columns
Presolve time: 0.01s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.01 seconds (0.00 work units)
Thread count was 1 (of 8 available processors)

Solution count 2: 9.75266e+07 -0 

Optimal solution found (tolerance 1.00e-04)
Best objective 9.752656782790e+07, best bound 9.752656782790e+07, gap 0.0000%
Gurobi Optimizer version 9.5.2 build v9.5.2rc0 (mac64[rosetta2])
Thr

In [349]:
total_profit/row

942012.541434074

SAA

In [350]:
# gurobi
from gurobipy import *

total_profit = 0
row = 0
for point in range(new.shape[0]):
    # get weekly sales for those values
    n20 = y_train_total
    # reset index
    n20 = n20.reset_index()
    # drop index
    n20 = n20.drop(['index'], axis=1)
    # Create a new model
    m = Model("mip1")
    # variable z
    z = m.addVar(vtype=GRB.CONTINUOUS, name="z", lb=0)
    # variable q
    q = m.addVar(vtype=GRB.CONTINUOUS, name="q", lb=0)
    # variable r that is array of size n20
    #r = m.addVars(n20.shape[0], vtype=GRB.CONTINUOUS, name="r", lb=0)
    # variable p - vector size(n20)
    sold = m.addVars(n20.shape[0], vtype=GRB.CONTINUOUS, name="p", lb=0)
    # variable r - vector size(n20)
    #unmet = m.addVars(n20.shape[0], vtype=GRB.CONTINUOUS, name="unment", lb=0)
    # objective, for i in n20, z*(100/19)-min(i,z*3)
    m.setObjective(quicksum(sold[i]-z*(19/100) for i in range(n20.shape[0])), GRB.MAXIMIZE)
    # p[i] = min(i,z*3)
    m.addConstrs((sold[i] == min_(q, constant=n20.loc[i]) for i in range(n20.shape[0])), "c")
    # z = q+r
    #m.addConstrs((unmet[i] == min_(r[i], constant=0) for i in range(n20.shape[0])), "c")
    #m.addConstr((r[i] == q - n20.loc[i] for i in range(n20.shape[0])), "c")
    # z = q
    m.addConstr(z*3 == q, "c2")

    # Optimize model
    m.optimize()
    
    profit = min(q.x, new.loc[row]['Weekly_Sales']) - z.x*(19/100)
    row += 1
    total_profit += profit


Gurobi Optimizer version 9.5.2 build v9.5.2rc0 (mac64[rosetta2])
Thread count: 8 physical cores, 8 logical processors, using up to 8 threads
Optimize a model with 1 rows, 5762 columns and 2 nonzeros
Model fingerprint: 0xe87b0c79
Model has 5760 general constraints
Variable types: 5762 continuous, 0 integer (0 binary)
Coefficient statistics:
  Matrix range     [1e+00, 3e+00]
  Objective range  [1e+00, 1e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [0e+00, 0e+00]
  GenCon const rng [2e+05, 4e+06]
Found heuristic solution: objective -0.0000000
Presolve removed 1 rows and 5762 columns
Presolve time: 0.06s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.07 seconds (0.01 work units)
Thread count was 1 (of 8 available processors)

Solution count 2: 5.2209e+09 -0 

Optimal solution found (tolerance 1.00e-04)
Best objective 5.220897436914e+09, best bound 5.220897436914e+09, gap 0.0000%
Gurobi Optimizer version 9.5.2 build v9.5.2rc0 (mac64[rosetta

In [351]:
total_profit/row

893400.4267518523

In [146]:
(902669.0376399072 - 890890.9153611112)/890890.9153611112

0.013220611048684825

SAA of previous by store

In [354]:
new.loc[1]['Store']

1.0

In [356]:
# gurobi
from gurobipy import *

total_profit = 0
row = 0
for node in nodes:
    # get weekly sales for those values
    n20 = y_train_total[X_train_total['Store']== new.loc[node]['Store']]
    # reset index
    n20 = n20.reset_index()
    # drop index
    n20 = n20.drop(['index'], axis=1)
    # Create a new model
    m = Model("mip1")
    # variable z
    z = m.addVar(vtype=GRB.CONTINUOUS, name="z", lb=0)
    # variable q
    q = m.addVar(vtype=GRB.CONTINUOUS, name="q", lb=0)
    # variable r that is array of size n20
    #r = m.addVars(n20.shape[0], vtype=GRB.CONTINUOUS, name="r", lb=0)
    # variable p - vector size(n20)
    sold = m.addVars(n20.shape[0], vtype=GRB.CONTINUOUS, name="p", lb=0)
    # variable r - vector size(n20)
    #unmet = m.addVars(n20.shape[0], vtype=GRB.CONTINUOUS, name="unment", lb=0)
    # objective, for i in n20, z*(100/19)-min(i,z*3)
    m.setObjective(quicksum(sold[i]-z*(19/100) for i in range(n20.shape[0])), GRB.MAXIMIZE)
    # p[i] = min(i,z*3)
    m.addConstrs((sold[i] == min_(q, constant=n20.loc[i]) for i in range(n20.shape[0])), "c")
    # z = q+r
    #m.addConstrs((unmet[i] == min_(r[i], constant=0) for i in range(n20.shape[0])), "c")
    #m.addConstr((r[i] == q - n20.loc[i] for i in range(n20.shape[0])), "c")
    # z = q
    m.addConstr(z*3 == q, "c2")

    # Optimize model
    m.optimize()
    
    profit = min(q.x, new.loc[row]['Weekly_Sales']) - z.x*(19/100)
    row += 1
    total_profit += profit


IndexingError: Unalignable boolean Series provided as indexer (index of the boolean Series and of the indexed object do not match).

In [12]:
total_profit/row

884095.6701555555

In [18]:
(910783.6065281482 - 884095.6701555555)/884095.6701555555

0.030186706341291083

regress and compare

In [164]:
# go through row in new
rcprofit = 0
for row in range(new.shape[0]):
    # use cart model to predict new row
    z = cart_model.predict(new.loc[i].drop(['Weekly_Sales']).values.reshape(1, -1))
    rcprofit += min(new.loc[row]['Weekly_Sales'],z)-z*(19/100)

print(rcprofit/new.shape[0])


[673662.38452821]


/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but DecisionTreeRegressor was fitted with feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but DecisionTreeRegressor was fitted with feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but DecisionTreeRegressor was fitted with feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but DecisionTreeRegressor was fitted with feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but DecisionTreeRegressor was fitted with feature names
  

In [59]:
(901480.9226480555-673662.38452821)/673662.38452821

0.3381790988365707

# Random Forest

In [13]:
# random forest model
from sklearn.ensemble import RandomForestRegressor

rf_model = RandomForestRegressor(random_state = 42, n_estimators = 50, min_samples_leaf = 5)
rf_model.fit(X_train, y_train)
y_pred = rf_model.predict(X_test)


In [14]:
# score the model
from sklearn.metrics import mean_squared_error, r2_score
# set random seed
np.random.seed(123)
print('MSE: ', mean_squared_error(y_test, y_pred))
print('R2: ', r2_score(y_test, y_pred))

MSE:  83557254624.17278
R2:  0.7466187227955026


In [76]:
from random import sample


In [78]:
X_test_100 = X_test.sample(n=100)
y_test_100 = y_test[X_test_100.index]

In [81]:
y_test_100 = y_test_100.reset_index()

In [15]:
# gurobi
from gurobipy import *
total_profit = 0
ppn = np.zeros((new.shape[0], 50))
for t in range(50):
    row = 0
    nodes = rf_model.estimators_[t].apply(new.drop(['Weekly_Sales'], axis=1))
    for node in nodes:
        # get weekly sales for those values
        n20 = y_train[rf_model.estimators_[t].apply(X_train) == node]
        # reset index
        n20 = n20.reset_index()
        # drop index
        n20 = n20.drop(['index'], axis=1)
        # Create a new model
        m = Model("mip1")
        # variable z
        z = m.addVar(vtype=GRB.CONTINUOUS, name="z", lb=0)
        # variable q
        q = m.addVar(vtype=GRB.CONTINUOUS, name="q", lb=0)
        # variable r that is array of size n20
        #r = m.addVars(n20.shape[0], vtype=GRB.CONTINUOUS, name="r", lb=0)
        # variable p - vector size(n20)
        sold = m.addVars(n20.shape[0], vtype=GRB.CONTINUOUS, name="p", lb=0)
        # variable r - vector size(n20)
        #unmet = m.addVars(n20.shape[0], vtype=GRB.CONTINUOUS, name="unment", lb=0)
        # objective, for i in n20, z*(100/19)-min(i,z*3)
        m.setObjective(quicksum(sold[i]-z*(19/100) for i in range(n20.shape[0])), GRB.MAXIMIZE)
        # p[i] = min(i,z*3)
        m.addConstrs((sold[i] == min_(q, constant=n20.loc[i]) for i in range(n20.shape[0])), "c")
        # z = q+r
        #m.addConstrs((unmet[i] == min_(r[i], constant=0) for i in range(n20.shape[0])), "c")
        #m.addConstr((r[i] == q - n20.loc[i] for i in range(n20.shape[0])), "c")
        # z = q
        m.addConstr(z*3 == q, "c2")

        # Optimize model
        m.optimize()
        
        #profit = min(q.x, new.loc[row]['Weekly_Sales']) - z.x*(19/100)
        ppn[row][t] = z.x
        row += 1

Gurobi Optimizer version 9.5.2 build v9.5.2rc0 (mac64[rosetta2])
Thread count: 8 physical cores, 8 logical processors, using up to 8 threads
Optimize a model with 1 rows, 19 columns and 2 nonzeros
Model fingerprint: 0x82e5d95e
Model has 17 general constraints
Variable types: 19 continuous, 0 integer (0 binary)
Coefficient statistics:
  Matrix range     [1e+00, 3e+00]
  Objective range  [1e+00, 3e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [0e+00, 0e+00]
  GenCon const rng [1e+06, 2e+06]
Found heuristic solution: objective -0.0000000
Presolve removed 1 rows and 19 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.01 seconds (0.00 work units)
Thread count was 1 (of 8 available processors)

Solution count 2: 2.38285e+07 -0 

Optimal solution found (tolerance 1.00e-04)
Best objective 2.382848536250e+07, best bound 2.382848536250e+07, gap 0.0000%
Gurobi Optimizer version 9.5.2 build v9.5.2rc0 (mac64[rosetta2])
Thr

/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-

  Bounds range     [0e+00, 0e+00]
  RHS range        [0e+00, 0e+00]
  GenCon const rng [5e+05, 8e+05]
Found heuristic solution: objective -0.0000000
Presolve removed 1 rows and 12 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.03 seconds (0.00 work units)
Thread count was 1 (of 8 available processors)

Solution count 2: 5.86516e+06 -0 

Optimal solution found (tolerance 1.00e-04)
Best objective 5.865164204667e+06, best bound 5.865164204667e+06, gap 0.0000%
Gurobi Optimizer version 9.5.2 build v9.5.2rc0 (mac64[rosetta2])
Thread count: 8 physical cores, 8 logical processors, using up to 8 threads
Optimize a model with 1 rows, 12 columns and 2 nonzeros
Model fingerprint: 0xeb71e2c7
Model has 10 general constraints
Variable types: 12 continuous, 0 integer (0 binary)
Coefficient statistics:
  Matrix range     [1e+00, 3e+00]
  Objective range  [1e+00, 2e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [0e+00, 0e+00]


/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-

Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.00 seconds (0.00 work units)
Thread count was 1 (of 8 available processors)

Solution count 2: 7.28847e+06 -0 

Optimal solution found (tolerance 1.00e-04)
Best objective 7.288473245200e+06, best bound 7.288473245200e+06, gap 0.0000%
Gurobi Optimizer version 9.5.2 build v9.5.2rc0 (mac64[rosetta2])
Thread count: 8 physical cores, 8 logical processors, using up to 8 threads
Optimize a model with 1 rows, 17 columns and 2 nonzeros
Model fingerprint: 0x17462819
Model has 15 general constraints
Variable types: 17 continuous, 0 integer (0 binary)
Coefficient statistics:
  Matrix range     [1e+00, 3e+00]
  Objective range  [1e+00, 3e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [0e+00, 0e+00]
  GenCon const rng [5e+05, 6e+05]
Found heuristic solution: objective -0.0000000
Presolve removed 1 rows and 17 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex 

...

/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-

Gurobi Optimizer version 9.5.2 build v9.5.2rc0 (mac64[rosetta2])
Thread count: 8 physical cores, 8 logical processors, using up to 8 threads
Optimize a model with 1 rows, 11 columns and 2 nonzeros
Model fingerprint: 0x253d1b2d
Model has 9 general constraints
Variable types: 11 continuous, 0 integer (0 binary)
Coefficient statistics:
  Matrix range     [1e+00, 3e+00]
  Objective range  [1e+00, 2e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [0e+00, 0e+00]
  GenCon const rng [8e+05, 9e+05]
Found heuristic solution: objective -0.0000000
Presolve removed 1 rows and 11 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.00 seconds (0.00 work units)
Thread count was 1 (of 8 available processors)

Solution count 2: 7.35754e+06 -0 

Optimal solution found (tolerance 1.00e-04)
Best objective 7.357538156900e+06, best bound 7.357538156900e+06, gap 0.0000%
Gurobi Optimizer version 9.5.2 build v9.5.2rc0 (mac64[rosetta2])
Thre

/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but DecisionTreeRegressor was fitted without feature names
  warnings.warn(
/Users/zachwayne/opt/anaconda3/lib/python3.9/site-

Gurobi Optimizer version 9.5.2 build v9.5.2rc0 (mac64[rosetta2])
Thread count: 8 physical cores, 8 logical processors, using up to 8 threads
Optimize a model with 1 rows, 12 columns and 2 nonzeros
Model fingerprint: 0xd9cbcafe
Model has 10 general constraints
Variable types: 12 continuous, 0 integer (0 binary)
Coefficient statistics:
  Matrix range     [1e+00, 3e+00]
  Objective range  [1e+00, 2e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [0e+00, 0e+00]
  GenCon const rng [9e+05, 1e+06]
Found heuristic solution: objective -0.0000000
Presolve removed 1 rows and 12 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.01 seconds (0.00 work units)
Thread count was 1 (of 8 available processors)

Solution count 2: 8.79418e+06 -0 

Optimal solution found (tolerance 1.00e-04)
Best objective 8.794180705667e+06, best bound 8.794180705667e+06, gap 0.0000%
Gurobi Optimizer version 9.5.2 build v9.5.2rc0 (mac64[rosetta2])
Thr

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [16]:
# get average for each row of ppn
total_profit = 0
for row in range(ppn.shape[0]):
    z = np.mean(ppn[row])
    total_profit += min(new.loc[row]['Weekly_Sales'],z*3)-z*(19/100)




In [17]:
total_profit/new.shape[0]

912148.1044346371

In [131]:
(910299.1663227688 - 890890.9153611112)/890890.9153611112

0.021785215930494397